In [13]:
!pip3 install pandas

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.


### Get the filelist

For the full results.json

In [14]:
import glob

# Specify the path to the folder containing the results.json files
folder_path = "lm-eval-output"

# Use glob to find all the results.json files
results_json_files = glob.glob(f"{folder_path}/**/results.json", recursive=True)

# Show total number of results.json files found
print(f"Found {len(results_json_files)} results.json files")


Found 3025 results.json files


### Process all the results.json

One file at a time

In [15]:
import json

# Global result map if it's not set
if 'global_result_map' not in globals():
    global_result_map = {}

#
# Function to process the results.json file
#
def process_results_json(file_path):
    with open(file_path) as f:
        data = json.load(f)

    # Model args, presplit by ','
    model_args = data['config']['model_args'].split(',')

    # Extract the pretrained value from config.model_args
    modelname = model_args[0].split('=')[1]

    # Opt array
    confArgsArr = model_args[1:]

    # Sort the opt array
    confArgsArr.sort()
    # Convert it to a string
    confStr = ','.join(confArgsArr)

    # Convert the option array of key=value strings to a dictionary
    confObj = { }
    for o in confArgsArr:
        k, v = o.split('=')
        confObj[k] = v
    
    # Create a dictionary to store the results, or use the existing one if it exists
    if modelname in global_result_map:
        modelObj = global_result_map[modelname]
    else:
        modelObj = {
            'name': modelname,
            'config': { }
        }
    
    # Get the opt object for the model
    if confStr in modelObj['config']:
        confSet = modelObj['config'][confStr]
    else:
        confSet = {
            'confStr': confStr,
            'confObj': confObj,
            'results': {},
            'groups': {}
        }

    # Iterate over the results and extract the result object for each test/group
    if 'results' in data:
        for test, result in data['results'].items():
            confSet['results'][test] = result
    if 'groups' in data:
        for test, result in data['groups'].items():
            confSet['groups'][test] = result
    
    # Update the global result map object
    modelObj['config'][confStr] = confSet
    global_result_map[modelname] = modelObj
    return modelObj

# Lets test the function with the first results.json file
first_result = process_results_json(results_json_files[0])
print(f"Processed example: ", first_result)


Processed example:  {'name': 'mistralai/Mistral-7B-v0.1', 'config': {'dtype=bfloat16,trust_remote_code=True': {'confStr': 'dtype=bfloat16,trust_remote_code=True', 'confObj': {'dtype': 'bfloat16', 'trust_remote_code': 'True'}, 'results': {'cola': {'mcc,none': -0.05103445794224817, 'mcc_stderr,none': 0.03076801823137936, 'alias': 'cola'}, 'anli': {'acc,none': 0.3803125, 'acc_stderr,none': 0.015133650384246593, 'alias': 'anli'}, 'anli_r1': {'acc,none': 0.377, 'acc_stderr,none': 0.01533317012577988, 'alias': ' - anli_r1'}, 'anli_r2': {'acc,none': 0.376, 'acc_stderr,none': 0.015325105508898125, 'alias': ' - anli_r2'}, 'anli_r3': {'acc,none': 0.38666666666666666, 'acc_stderr,none': 0.014063941778353468, 'alias': ' - anli_r3'}, 'wsc': {'acc,none': 0.40384615384615385, 'acc_stderr,none': 0.04834688952654018, 'alias': ' - wsc'}, 'lambada_cloze': {'perplexity,none': 92.9621493847383, 'perplexity_stderr,none': 4.749192287461508, 'acc,none': 0.08354356685425965, 'acc_stderr,none': 0.01735953787342

In [16]:
# Lets reset and reprocess all the results.json files
global_result_map = {}

# Process all the results.json files
for file in results_json_files:
    process_results_json(file)

# Show high level list of models
print(f"Found {len(global_result_map)} models")
print(f"Models: \n{list(global_result_map.keys())}")

# Save the result map to a file
with open('summary/compiled-lm-eval-results.json', 'w') as f:
    json.dump(global_result_map, f, sort_keys=True, indent='\t')

# Echo that its been saved to json
print(f"Saved to compiled-lm-eval-results.json")

Found 57 models
Models: 
['mistralai/Mistral-7B-v0.1', 'mosaicml/mpt-7b-instruct', 'mosaicml/mpt-7b', 'mosaicml/mpt-7b-chat', 'bigscience/bloom-7b1', 'bigscience/bloomz-7b1-mt', 'bigscience/bloomz-7b1', 'EleutherAI/pythia-2.8b', 'EleutherAI/pythia-1.4b', 'EleutherAI/gpt-j-6b', 'EleutherAI/pythia-6.9b', 'google/flan-t5-base', 'google/gemma-2b', 'google/gemma-2b-it', 'google/gemma-7b', 'google/gemma-7b-it', 'google/flan-t5-large', 'microsoft/phi-1_5', 'microsoft/phi-2', 'microsoft/phi-1', 'allenai/OLMo-7B', 'TinyLlama/TinyLlama-1.1B-intermediate-step-1431k-3T', 'TinyLlama/TinyLlama-1.1B-Chat-v1.0', 'RWKV/rwkv-5-world-1b5', 'RWKV/rwkv-5-world-3b', 'RWKV/rwkv-4-world-3b', 'RWKV/rwkv-4-world-1b5', 'RWKV/v5-Eagle-7B-HF', 'RWKV/rwkv-4-world-7b', './rwkv-x-dev/chunk4-0_85_pth', './rwkv-x-dev/chunk1-0_8_pth', './rwkv-x-dev/chunk0-0_8_pth', './rwkv-x-dev/chunk2-0_8_pth', './rwkv-x-dev/chunk3-0_8_pth', './rwkv-x-dev/chunk7-2-0_85_pth', './rwkv-x-dev/chunk5-0_85_pth', './rwkv-x-dev/RWKV-5-World-1B

### Convert the results into CSV table formats

In [17]:
# Lets convert this into a table, which we will display in this notebook, and save as a CSV
import pandas as pd

##################################################
#
#  Utility functions
#
##################################################

# Check if the given name string, is within the list, including "*" wildcard
def is_in_list(name, list):
    for n in list:
        if n[-1] == '*':
            if name.startswith(n[:-1]):
                return True
        elif n == name:
            return True
    return False

# Is in inclusion exclusion list pair
def is_in_list_pair(name, inList, exList):
    if not is_in_list(name, inList):
        return False
    if is_in_list(name, exList):
        return False
    return True

# Prepare a single test/group result object
# By applying common filtering and formatting changes
def prepare_test_result(result):
    # The reutrn object
    ret = {}
    # Iterate the result key/value
    for k, v in result.items():
        # Skip if its alias
        if k == 'alias':
            continue

        # If the key ends with ",none", drop the ",none"
        if k.endswith(',none'):
            k = k[:-5]
        
        # Save the result
        ret[k] = v
    
    # Return the result
    return ret

##################################################
#
#  Generate the result
#
##################################################

# Create a list of rows for the table
def generate_result_table(
    inConfig = { "dtype": "bfloat16" },

    # Models to include/exclude
    inModels = ["*"],
    exModels = ["./rwkv-x-dev/*", "rwkv-x-dev"],

    # Results and groups to include
    inResults = [],
    inGroups = ["*"],

    # Exclude results and groups, applied after inResults and inGroups
    exResults = [],
    exGroups = [],

    # Sorted
    sort = False
):
    table_rows = []

    # Iterate over the models
    for model, modelObj in global_result_map.items():
        # Skip if not in the inModels or exModels
        if not is_in_list_pair(model, inModels, exModels):
            continue

        # Iterate over the configurations
        for confStr, confSet in modelObj['config'].items():
            # Get the confObj
            confObj = confSet['confObj']

            # Check if the inConfig, matches the confObj
            if inConfig:
                skip = False
                for k, v in inConfig.items():
                    if k not in confObj or confObj[k] != v:
                        skip = True
                        break
                if skip:
                    continue

            # Create a row object
            row = {
                'model': model,
                # 'config': confStr

                "avg_acc": 0.0,
                "avg_acc_stderr": 0.0,
            }

            # Total acc / acc_stderr
            acc_total = 0.0
            acc_count = 0
            acc_stderr_total = 0.0
            acc_stderr_count = 0

            # Add the groups
            for test, result in confSet['groups'].items():

                # Skip if not in the inGroups or exGroups
                if not is_in_list_pair(test, inGroups, exGroups):
                    continue

                # Filter the result obj
                cleanResult = prepare_test_result(result)

                # Add the result to the row, as seperate columns for each key
                for k, v in cleanResult.items():
                    row[f"{test} ({k})"] = v

                    if k == 'acc':
                        acc_total += v
                        acc_count += 1
                    elif k == 'acc_stderr':
                        acc_stderr_total += v
                        acc_stderr_count += 1

            # Add the results
            for test, result in confSet['results'].items():

                # Skip if not in the inResults or exResults
                if not is_in_list_pair(test, inResults, exResults):
                    continue

                # Filter the result obj
                cleanResult = prepare_test_result(result)

                # Add the result to the row, as seperate columns for each key
                for k, v in cleanResult.items():
                    row[f"{test} ({k})"] = v

                    if k == 'acc':
                        acc_total += v
                        acc_count += 1
                    elif k == 'acc_stderr':
                        acc_stderr_total += v
                        acc_stderr_count += 1
                
            # Add the avg acc and acc_stderr
            if acc_count > 0:
               row["avg_acc"] = acc_total / acc_count
            if acc_stderr_count > 0:
                row["avg_acc_stderr"] = acc_stderr_total / acc_stderr_count

            # Append the row to the table
            table_rows.append(row)

    # Create a dataframe from the table rows
    df = pd.DataFrame(table_rows)

    # Sort by avg_acc
    if sort:
        df = df.sort_values(by='avg_acc', ascending=False)

    # Show the dataframe
    return df

# Generate the dataframe
df = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["xcopa"], inResults=[] )

# # Save the dataframe to a CSV file
# df.to_csv('summary/compiled-lm-eval-results.csv', index=False)

# Show results
df


model   avg_acc  \
0                           mistralai/Mistral-7B-v0.1  0.559455   
1                            mosaicml/mpt-7b-instruct  0.537091   
2                                     mosaicml/mpt-7b  0.536000   
3                                mosaicml/mpt-7b-chat  0.538000   
4                                bigscience/bloom-7b1  0.570909   
5                            bigscience/bloomz-7b1-mt  0.546000   
6                               bigscience/bloomz-7b1  0.547818   
7                              EleutherAI/pythia-2.8b  0.537455   
8                              EleutherAI/pythia-1.4b  0.526545   
9                                 EleutherAI/gpt-j-6b  0.544182   
10                             EleutherAI/pythia-6.9b  0.540545   
11                                google/flan-t5-base  0.510909   
12                                    google/gemma-2b  0.000000   
13                                 google/gemma-2b-it  0.000000   
14                                    google/gemma-7b  0.517636   
15                                 google/gemma-7b-it  0.517455   
16                               google/flan-t5-large  0.510545   
17                                  microsoft/phi-1_5  0.521636   
18                                    microsoft/phi-2  0.512182   
19                                    microsoft/phi-1  0.517636   
20                                    allenai/OLMo-7B  0.537818   
21  TinyLlama/TinyLlama-1.1B-intermediate-step-143...  0.529273   
22                 TinyLlama/TinyLlama-1.1B-Chat-v1.0  0.528909   
23                              RWKV/rwkv-5-world-1b5  0.579636   
24                               RWKV/rwkv-5-world-3b  0.590000   
25                               RWKV/rwkv-4-world-3b  0.575455   
26                              RWKV/rwkv-4-world-1b5  0.554000   
27                                RWKV/v5-Eagle-7B-HF  0.622364   
28                               RWKV/rwkv-4-world-7b  0.601455   
29          togethercomputer/RedPajama-INCITE-7B-Base  0.525455   
30      togethercomputer/RedPajama-INCITE-7B-Instruct  0.528545   
31          togethercomputer/RedPajama-INCITE-7B-Chat  0.535455   
32                                  facebook/opt-2.7b  0.521818   
33                                  facebook/opt-6.7b  0.522909   
34                                  facebook/opt-1.3b  0.521818   
35                          tiiuae/falcon-7b-instruct  0.536727   
36                                tiiuae/falcon-rw-1b  0.522545   
37                                tiiuae/falcon-rw-7b  0.535818   
38                                   tiiuae/falcon-7b  0.559636   
39                                huggyllama/llama-7b  0.541818   
40                      meta-llama/Llama-2-7b-chat-hf  0.559818   
41                           meta-llama/Llama-2-7b-hf  0.566727   

    avg_acc_stderr  xcopa (acc)  xcopa (acc_stderr)  
0         0.053879     0.559455            0.053879  
1         0.041919     0.537091            0.041919  
2         0.042339     0.536000            0.042339  
3         0.047059     0.538000            0.047059  
4         0.061359     0.570909            0.061359  
5         0.038321     0.546000            0.038321  
6         0.038920     0.547818            0.038920  
7         0.026941     0.537455            0.026941  
8         0.027441     0.526545            0.027441  
9         0.034404     0.544182            0.034404  
10        0.029689     0.540545            0.029689  
11        0.006743     0.510909            0.006743  
12        0.000000          NaN                 NaN  
13        0.000000          NaN                 NaN  
14        0.006740     0.517636            0.006740  
15        0.006742     0.517455            0.006742  
16        0.006743     0.510545            0.006743  
17        0.026198     0.521636            0.026198  
18        0.029742     0.512182            0.029742  
19        0.029612     0.517636            0.029612  
20        0.034147     0.537818 

In [18]:
##################################################
#
#  Build the various subsets
#
##################################################

# Overall results
all_results = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"] )
all_results.to_csv('summary/bf16-all-results-and-groups.csv', index=False)

# Multilang results
multiLang_tTest = ["xcopa_*", "xnli_*", "xstorycloze_*", "xwinograd_*", "lambada_openai_*",     "pawsx_*"]
multiLang_tGrps = ["xcopa",   "xnli",   "xstorycloze",   "xwinograd",   "lambada_multilingual", "pawsx"]
# Both test and groups, merged into a single list
multiLang_joint = multiLang_tTest + multiLang_tGrps

multilang_grp = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=[] )
multilang_test = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=multiLang_tTest )
multilang_grp.to_csv('summary/bf16-multilang-summary.csv', index=False)
multilang_test.to_csv('summary/bf16-multilang-results.csv', index=False)

multilang_grp_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=[], sort=True )
multilang_grp_sorted.to_csv('summary/bf16-sorted-multilang-summary.csv', index=False)

# RWKV perf tracking
rwkv_multilang_grp_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=[], exModels=[], inModels=["./rwkv-x-dev/*", "rwkv-x-dev/*", "RWKV/*"], sort=True )
rwkv_multilang_grp_sorted.to_csv('summary/rwkv-x-dev-bf16-sorted-multilang-summary.csv', index=False)

# All other results
eng_grp = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=[], exGroups=multiLang_joint, exResults=multiLang_joint )
eng_grp_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=[], exGroups=multiLang_joint, exResults=multiLang_joint, sort=True )
eng_test = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], exGroups=multiLang_joint, exResults=multiLang_joint )
eng_test_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], exGroups=multiLang_joint, exResults=multiLang_joint, sort=True )

eng_grp.to_csv('summary/bf16-eng-summary.csv', index=False)
eng_test.to_csv('summary/bf16-eng-results.csv', index=False)
eng_test_sorted.to_csv('summary/bf16-sorted-eng-results.csv', index=False)
eng_grp_sorted.to_csv('summary/bf16-sorted-eng-summary.csv', index=False)

# English focused subset
eng_focus_tGrps=["anli", "glue", "truthfulqa", "lambada", "cmmlu", "pythia", "mmlu",    "blimp", "record", "np_open", "piqa", "copa", "sciq"]
eng_focus_tTest=["blimp", "arc_*", "logiqa", "winogrande", "openbookqa", "hellaswag",   "blimp", "record", "np_open", "piqa", "copa", "sciq"]
eng_focus = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=eng_focus_tGrps, inResults=eng_focus_tTest )
eng_focus_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=eng_focus_tGrps, inResults=eng_focus_tTest, sort=True )
eng_focus.to_csv('summary/bf16-eng-focus.csv', index=False)
eng_focus_sorted.to_csv('summary/bf16-sorted-eng-focus.csv', index=False)

# RWKV perf tracking
rwkv_eng_focus_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=eng_focus_tGrps, inResults=eng_focus_tTest, exModels=[], inModels=["./rwkv-x-dev/*", "rwkv-x-dev/*", "RWKV/*"], sort=True )
rwkv_eng_focus_sorted.to_csv('summary/rwkv-x-dev-bf16-sorted-eng-focus.csv', index=False)

# List the files
!ls -lh summary

total 17424
-rw-r--r--@ 1 picocreator  staff   1.0M Feb 28 08:55 bf16-all-results-and-groups.csv
-rw-r--r--@ 1 picocreator  staff    64K Feb 28 08:55 bf16-eng-focus.csv
-rw-r--r--@ 1 picocreator  staff   920K Feb 28 08:55 bf16-eng-results.csv
-rw-r--r--@ 1 picocreator  staff    77K Feb 28 08:55 bf16-eng-summary.csv
-rw-r--r--@ 1 picocreator  staff    96K Feb 28 08:55 bf16-multilang-results.csv
-rw-r--r--@ 1 picocreator  staff    14K Feb 28 08:55 bf16-multilang-summary.csv
-rw-r--r--@ 1 picocreator  staff    64K Feb 28 08:55 bf16-sorted-eng-focus.csv
-rw-r--r--@ 1 picocreator  staff   920K Feb 28 08:55 bf16-sorted-eng-results.csv
-rw-r--r--@ 1 picocreator  staff    77K Feb 28 08:55 bf16-sorted-eng-summary.csv
-rw-r--r--@ 1 picocreator  staff    14K Feb 28 08:55 bf16-sorted-multilang-summary.csv
-rw-r--r--  1 picocreator  staff   4.6M Feb 28 08:55 compiled-lm-eval-results.json
-rw-r--r--@ 1 picocreator  staff    31K Feb 28 08:55 rwkv-x-dev-bf16-sorted-eng-focus.csv
-rw-r--r--@ 1 picocrea